# 3-4. 深層学習の基礎と展望 - 学習用データと学習済みモデル
単語をベクトル化する有名な手法としてWord2Vecというものがある．これは単語を類似度に紐づくベクトルに埋め込むことができるという面白いモデルである．これは目的に応じて自分でコーパス（学習用の文章を大量に集めたもの）を用意してモデルの構築・学習を行うこともできるが，いちからモデルを学習しようとすると膨大な量のコーパスが必要になる．

あまり大きなコーパスが用意できない場合には，事前学習済みのモデルに対して追加で学習を行い，パラメータを微調整することで対応することもできる．

本節では，ゲームパッケージのタイトル群に登場する単語を学習済みモデルに追加で学習させることで，少ない学習量でもゲームタイトル的に近い意味を持つ単語が出力されるようにしよう．

## 学習用データの作成
[メディア芸術データベース・ラボ](https://mediag.bunka.go.jp/madb_lab/)上で提供されている[SPARQLクエリサービス](https://mediag.bunka.go.jp/madb_lab/lod/sparql/)を利用して，ゲームパッケージのデータを取得していく．


以下のコードを[SPARQLクエリサービス](https://mediag.bunka.go.jp/madb_lab/lod/sparql/)上に入力して実行する，または入力を省略した[こちらのURL](https://mediag.bunka.go.jp/madb_lab/lod/sparql/#query=PREFIX%20ma%3A%20%3Chttps%3A%2F%2Fmediaarts-db.bunka.go.jp%2Fdata%2Fproperty%23%3E%0APREFIX%20rdfs%3A%20%20%20%3Chttp%3A%2F%2Fwww.w3.org%2F2000%2F01%2Frdf-schema%23%3E%0APREFIX%20schema%3A%20%3Chttps%3A%2F%2Fschema.org%2F%3E%20SELECT%20%3F%E3%83%A9%E3%83%99%E3%83%AB%20%3F%E7%99%BA%E8%A1%8C%E8%80%85%20%3F%E3%83%97%E3%83%A9%E3%83%83%E3%83%88%E3%83%95%E3%82%A9%E3%83%BC%E3%83%A0%20%3F%E3%83%AC%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5%0AWHERE%20%7B%0A%20%20%3F%E3%82%A2%E3%82%A4%E3%83%86%E3%83%A0%0A%20%20%20%20%20%20%20%20schema%3Agenre%20%22%E3%82%B2%E3%83%BC%E3%83%A0%E3%83%91%E3%83%83%E3%82%B1%E3%83%BC%E3%82%B8%22%3B%0A%20%20%20%20%20%20%20%20schema%3AcontentRating%20%3F%E3%83%AC%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%3B%0A%20%20%20%20%20%20%20%20schema%3AgamePlatform%20%3F%E3%83%97%E3%83%A9%E3%83%83%E3%83%88%E3%83%95%E3%82%A9%E3%83%BC%E3%83%A0%3B%0A%20%20%20%20%20%20%20%20schema%3Apublisher%20%3F%E7%99%BA%E8%A1%8C%E8%80%85%3B%0A%20%20%20%20%20%20%20%20rdfs%3Alabel%20%3F%E3%83%A9%E3%83%99%E3%83%AB%3B%0A%20%20%20%20%20%20%20%20ma%3AdatePublished%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5.%0A%7D&endpoint=https%3A%2F%2Fmediag.bunka.go.jp%2Fsparql&requestMethod=POST&tabTitle=Query&headers=%7B%7D&contentTypeConstruct=application%2Fn-triples%2C*%2F*%3Bq%3D0.9&contentTypeSelect=application%2Fsparql-results%2Bjson%2C*%2F*%3Bq%3D0.9&outputFormat=table)から実行してデータを取得できる．


取得したCSVファイルを「ゲームパッケージ.csv」として保存し，このノートブック上にアップロードしよう．

※「3-4. ディープニューラルネットワーク（DNN）」，「3-6. 決定木」，「3-6. サポートベクターマシン」，「3-7. 形態素解析」，「3-7. かな漢字変換」，「3-7. 表現学習」と同じデータセットを作成するため，もし同じものを持っている場合は以下の取得作業は不要なので，そちらをアップロードしよう．

```
PREFIX ma: <https://mediaarts-db.bunka.go.jp/data/property#>
PREFIX rdfs:   <http://www.w3.org/2000/01/rdf-schema#>
PREFIX schema: <https://schema.org/> SELECT ?ラベル ?発行者 ?プラットフォーム ?レーティング ?公開年月日
WHERE {
  ?アイテム
        schema:genre "ゲームパッケージ";
        schema:contentRating ?レーティング;
        schema:gamePlatform ?プラットフォーム;
        schema:publisher ?発行者;
        rdfs:label ?ラベル;
        ma:datePublished ?公開年月日.
}
```

取得したデータセットを，Python上で扱いやすい形にしていく．
pandasというライブラリを用いて，csv形式のファイルの中身をDataFrameという型に変換し，扱っていく．

In [1]:
import pandas as pd
games = pd.read_csv("/content/ゲームパッケージ.csv")
games = games.drop_duplicates()
games = games.reset_index(drop=True)
games

ラベル  \
0                           Dance Dance Revolution GB2   
1                                     プロ野球 ファミスタ リターンズ   
2                                      プロ野球 ファミスタ 2011   
3                                              フロッガー3D   
4                                           ブレイブリーセカンド   
...                                                ...   
21976                 バイオショック インフィニット PlayStation Now版   
21977  バイオハザード リベレーションズ アンベールド エディション PlayStation Now版   
21978                           巫剣神威控 PlayStation Now版   
21979                 ネバーエンディング ナイトメア PlayStation Now版   
21980                   雷電IV OverKill PlayStation Now版   

                           発行者       プラットフォーム            レーティング       公開年月日  
0                      コナミ株式会社         ゲームボーイ  CERO D (17才以上対象)  2000-11-16  
1        株式会社バンダイナムコエンターテインメント      ニンテンドー3DS    CERO A (全年齢対象)  2015-10-08  
2              株式会社バンダイナムコゲームス      ニンテンドー3DS    CERO A (全年齢対象)  2011-03-31  
3         株式会社コナミデジタルエンタテインメント      ニンテンドー3DS    CERO A (全年齢対象)  2011-09-22  
4              株式会社スクウェア・エニックス      ニンテンドー3DS  CERO C (15才以上対象)  2015-04-23  
...                        ...            ...               ...         ...  
21976  テイクツー・インタラクティブ・ジャパン合同会社  プレイステーション Now  CERO D (17才以上対象)  2017-09-19  
21977                 株式会社カプコン  プレイステーション Now  CERO D (17才以上対象)  2016-09-20  
21978           アクティブゲーミングメディア  プレイステーション Now  CERO C (15才以上対象)  2017-07-20  
21979           アクティブゲーミングメディア  プレイステーション Now  CERO D (17才以上対象)  2017-07-20  
21980                       モス  プレイステーション Now    CERO A (全年齢対象)  2017-02-21  

[21981 rows x 5 columns]

ゲームパッケージのタイトルを，単語の分かち書きにする．

In [2]:
# 必要なモジュールの読み込み
!pip install mecab-python3
!pip install unidic-lite
import MeCab
import re

# 分かち書きを行うインスタンスwakatiの作成
wakati = MeCab.Tagger('-Owakati')

# 分かち書きしたタイトルを格納するリスト
wakati_titles = []

for title in games['ラベル']:
  wakati_titles.append(wakati.parse(title).strip())

# w2vに追加学習させるコーパス
new_corpus = []
for wakati_title in wakati_titles:
  tmp = re.sub("\u3000|!|\?", "", wakati_title).split(" ")
  new_corpus.append([token for token in tmp if len(token) > 1]) # 単語長が２以上のもののみを学習対象にする


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 581.7/581.7 kB 11.7 MB/s eta 0:00:00 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.4/47.4 MB 16.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for unidic-lite: filename=unidic_lite-1.0.8-py3-none-any.whl size=47658817 sha256=a9a9a224d466416d551af5910ab035945d18dfc1ea28aab045cacd1a943e59b2
  Stored in directory: /root/.cache/pip/wheels/89/e8/68/f9ac36b8cc6c8b3c96888cd57434abed96595d444f42243853
Successfully built unidic-lite


In [3]:
print(new_corpus[0])

['Dance', 'Dance', 'Revolution', 'GB']


## 学習済みモデルのロード

In [4]:
#必要なモジュールの読み込み
!pip install --upgrade gensim
from gensim.models import word2vec

# 事前学習済みモデルのインストール
!wget "http://public.shiroyagi.s3.amazonaws.com/latest-ja-word2vec-gensim-model.zip"
!unzip "/content/latest-ja-word2vec-gensim-model.zip"

--2024-02-14 05:58:56--  http://public.shiroyagi.s3.amazonaws.com/latest-ja-word2vec-gensim-model.zip
Resolving public.shiroyagi.s3.amazonaws.com (public.shiroyagi.s3.amazonaws.com)... 52.219.136.205, 52.219.8.173, 52.219.16.213, ...
Connecting to public.shiroyagi.s3.amazonaws.com (public.shiroyagi.s3.amazonaws.com)|52.219.136.205|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 132936751 (127M) [application/zip]
Saving to: ‘latest-ja-word2vec-gensim-model.zip’

latest-ja-word2vec- 100%[===================>] 126.78M  19.5MB/s    in 7.4s    

2024-02-14 05:59:04 (17.0 MB/s) - ‘latest-ja-word2vec-gensim-model.zip’ saved [132936751/132936751]

Archive:  /content/latest-ja-word2vec-gensim-model.zip
  inflating: word2vec.gensim.model   
  inflating: word2vec.gensim.model.syn1neg.npy  
  inflating: word2vec.gensim.model.wv.syn0.npy  


In [5]:
# 事前学習済みモデルのロード
w2v_origin = word2vec.Word2Vec.load("/content/word2vec.gensim.model")

# こちらを追加学習用モデルにしていく
w2v = word2vec.Word2Vec.load("/content/word2vec.gensim.model")

In [6]:
# 新しいコーパスを追加で学習させる
w2v.build_vocab(new_corpus, update=True)
w2v.train(new_corpus, total_examples=w2v.corpus_count, epochs=w2v.epochs)

(227781, 521520)

In [7]:
# 学習前の「DS」に近い単語
print(w2v_origin.wv.most_similar("DS"))

[('PS2', 0.9018317461013794), ('PS3', 0.8976770639419556), ('PSP', 0.8939802050590515), ('GBA', 0.8769130706787109), ('PS4', 0.8751301169395447), ('SFC', 0.8686517477035522), ('3DS', 0.8658976554870605), ('PS Vita', 0.8649856448173523), ('ゲームキューブ', 0.8592252731323242), ('パワーアップキット', 0.8539624810218811)]


In [8]:
# 学習後の「DS」に近い単語
print(w2v.wv.most_similar("DS"))

[('DSi', 0.9567910432815552), ('ポータブル', 0.9450507164001465), ('DX', 0.9403018951416016), ('ウェア', 0.9384950399398804), ('Wii', 0.9258646965026855), ('パズル', 0.9234594106674194), ('ウォーズ', 0.9170921444892883), ('アドベンチャー', 0.9161989092826843), ('セレクション', 0.9157466292381287), ('EX', 0.9150858521461487)]


学習の前後で，近しい単語の種類が変わっていることがわかる．

元々のモデル上では，ゲームプラットフォームという意味において"DS"に近しいものが出力されている．

それに対しゲームタイトルをコーパスとして追加で学習したものでは，ゲームタイトルに（オマケ的に）よく登場する単語として"DS"に似たようなものが出力されている．

このように学習済みモデルを利用することで，自然言語処理としてはあまり大規模ではなかった`wakati_titles`のみでも直感的に意味の通る結果を得ることができる．